In [5]:
# vbgmm find only two non-negligeable clusters:

from visualization_fct import *
#from sklearn.mixture import VBGMM
from sklearn.mixture import BayesianGaussianMixture

from bokeh.io import output_notebook
output_notebook()
from bokeh.plotting import show  # output_file, save
# from bokeh.mpl import to_bokeh

from bokeh.resources import CDN
from bokeh.embed import file_html


import matplotlib.pyplot as plt  # , mpld3

without_CA = False
n_components = 4

data = pd.read_csv("../asm_data/asm_data_for_ml.txt", sep='\t')
del data['MJD']
# del data['error']
# del data['errorA']
# del data['errorB']
# del data['errorC']
data['rateCA'] = data.rateC / data.rateA
data_thr = mask(data, 'orbit')  # rm too large values except for 'orbit'

w = np.concatenate([np.array(data[name]).reshape(-1, 1)
                    for name in ['error', 'errorA', 'errorB', 'errorC']],
                   axis=1)
del data_thr['error']
del data_thr['errorA']
del data_thr['errorB']
del data_thr['errorC']


np.random.seed(0)

if without_CA:
    X = np.c_[data_thr.orbit, data_thr.rate, data_thr.rateA, data_thr.rateB,
              data_thr.rateC]
else:
    X = np.c_[data_thr.orbit, data_thr.rate, data_thr.rateA, data_thr.rateB,
              data_thr.rateC, data_thr.rateCA]
    
gmm = BayesianGaussianMixture(n_components=n_components, covariance_type='full')
gmm.fit(X)
preds = gmm.predict(X)
probs = gmm.predict_proba(X)

data_thr['preds'] = pd.Series(preds).astype("category")

color_key = ["red", "blue", "yellow", "grey", "black", "purple", "pink",
             "brown", "green", "orange"]  # Spectral9
color_key = color_key[:n_components+1]

print 'set(preds)=', set(preds)
print 'gmm.weights_=', gmm.weights_
print 'gmm.means_=', gmm.means_

means =  gmm.means_
covs = gmm.covariances_

Loading BokehJS ...

set(preds)= set([2, 3])
gmm.weights_= [  2.67262484e-06   2.67262484e-06   8.52907289e-01   1.47087366e-01]
gmm.means_= [[  0.50087323  31.77805602  12.4945139    9.31096515  10.57645264
    1.35705444]
 [  0.50087323  31.77805602  12.4945139    9.31096515  10.57645264
    1.35705444]
 [  0.50118226  25.23569212   7.81619625   7.32210027   9.89960397
    1.52609995]
 [  0.49908138  69.71318471  39.62118938  20.84316457  14.50108015
    0.37686391]]


In [6]:
if without_CA:
    covs_xy = None
    means_xy = None
else:
    x = 5
    y = 1
    covs_xy = [covs[j][[x, y]][:, [x, y]] for j in range(len(covs))]
    means_xy = [means[j][[x, y]] for j in range(len(covs))]
    
single_plot = bokeh_datashader_plot(data_thr, covs=covs_xy, means=means_xy,
                                    x_name='rateCA',
                                    y_name='rate',
                                    plot_width=900, plot_height=300,
                                    pixel_width=3000, pixel_height=1000,
                                    spread=True, color_key=color_key)
show(single_plot)